In [3]:
import numpy as np
import matplotlib.pyplot as plt
import scipy.odr as odr
from glob import glob
import re
%matplotlib inline

In [5]:
files = glob("*.csv")
files.sort()
for (i,file) in enumerate(files):
    print "%d, %s" % (i, file)
iFile = int(raw_input("Enter file number: "))
datafile = files[iFile]
fpData = open(datafile)
data = np.genfromtxt(datafile, comments='#', delimiter=',')
v0 = data[:,0]
v1 = data[:,1]
v2 = data[:,2]
voltage = data[:,3]
current = data[:,4]

# Create a name for the figure file
figFile = re.sub(r'csv$', "png", LEDdata.csv)
print "figFile = ", figFile

# Now go back and grab the first comment line
fpData = open(LEDdata.csv, 'r')
line = fpData.readline().strip()
figureTitle = line[2:]
print "figureTitle >%s<" % (figureTitle)
fpData.close()

0, LEDdata.csv


Enter file number:  0

In [2]:
fig = plt.figure(figsize=(15,5))
ax = fig.add_subplot(111)
ax.grid(True)
ax.set_title("Curretn vs Voltage" )
pl1 = ax.plot(voltage, current)

ax.set_xlabel('Voltage (V)')
ax.set_ylabel('current (mA)')

ax.plot(voltage, current, 'bo')


NameError: name 'plt' is not defined

### LED Model
Use an exponential model.
$$ I(V) =  e^{(V - V_f)/V_0} $$
where $V_f$ is the turn on voltage and $V_0$ sets the voltage scale.

In [3]:
def LEDModel(Params, V):
    V0 = Params[0]
    Vf = Params[1]
    return np.exp((V-Vf)/V0)

myModel = odr.Model(LEDModel)

myData = odr.RealData(voltage, current, sx=”Voltage Uncertainty”, sy=”Current Uncertainty”)

initParams = np.array([1.0,2.0])
myOdr = odr.ODR(myData, myModel, beta0=initParams)
myOutput = myOdr.run()
myOutput.pprint()
(V0_Fit, Vf_Fit) = myOutput.beta
(V0_SD, Vf_SD) = myOutput.sd_beta
resultStr = \
r"""$V_0$ = %.4f $\pm$ %.4f V
$V_f$ = %.4f $\pm$ %.4f V""" % (V0_Fit, V0_SD, Vf_Fit, Vf_SD)
print resultStr

SyntaxError: invalid syntax (<ipython-input-3-97738f0e54c6>, line 8)

In [0]:
fig = plt.figure(figsize=(15,5))
ax = fig.add_subplot(111)
ax.grid(True)
ax.set_title("Comment: %s" % (figureTitle))
ax.plot(voltage, current, 'b-', label='Data')
ax.set_xlabel('Voltage (V)')
ax.set_ylabel('current (mA)')

ax.plot(voltage, LEDModel(myOutput.beta, voltage), 'r-', label='Model')

ax.text(0, 0.7 * np.max(current), resultStr, size='large')

jnk = ax.legend()
fig.savefig(figFile)